In [9]:
import pandas as pd
import glob
import numpy
import csv
from nltk.tokenize import word_tokenize
import xlrd
import re
from nltk import bigrams
from nltk import ngrams
import operator
from collections import Counter
from nltk.corpus import stopwords
import string
import matplotlib.pyplot as plt

from random import randint
from numpy import array
from numpy import argmax
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense

In [10]:
data = pd.read_csv("dataset/final/all/trending.csv") 

In [11]:
data.head()

Date                                              Array
0  1/1/2011  [('#travel', 26), ('#news', 20), ('#guyana', 1...
1  1/2/2011  [('#travel', 45), ('#news', 16), ('#jobs', 12)...
2  1/3/2011  [('#travel', 72), ('#sgt11', 68), ('#news', 39...
3  1/4/2011  [('#travel', 90), ('#news', 30), ('#hotel', 23...
4  1/5/2011  [('#travel', 99), ('#news', 57), ('#gtnews', 4...

In [12]:
data.shape

(3174, 2)

In [13]:
from datetime import datetime
import ast

In [14]:
array = []
trendingTopicsAll = []
trendingIdsInEachDays = []
for index, row in data.iterrows():
    trendingIdsInEachDays.append([])
    date = datetime.strptime(row['Date'], '%m/%d/%Y').date()
    #print(date)
    testarray = ast.literal_eval(row['Array'])
    for x in testarray:
        if x[0] not in trendingTopicsAll:
            trendingTopicsAll.append(x[0])
        getIndex = trendingTopicsAll.index(x[0])
        trendingIdsInEachDays[index].append(getIndex)
print(len(trendingIdsInEachDays))

3174


In [15]:
print(trendingIdsInEachDays)

[[0, 1, 2, 3, 4, 5, 6, 7, 8, 9], [0, 1, 5, 2, 3, 4, 10, 11, 12, 13], [0, 14, 1, 15, 12, 4, 2, 3, 16, 17], [0, 1, 16, 12, 17, 18, 19, 4, 2, 3], [0, 1, 12, 20, 21, 16, 17, 4, 2, 3], [0, 1, 12, 16, 17, 15, 22, 20, 23, 24], [25, 0, 12, 16, 17, 1, 26, 24, 5, 27], [0, 28, 1, 29, 5, 14, 20, 30, 31, 13], [0, 1, 30, 32, 33, 34, 35, 36, 12, 29], [0, 1, 16, 12, 17, 29, 30, 28, 37, 38], [0, 16, 1, 17, 12, 20, 4, 39, 37, 2], [0, 12, 1, 16, 17, 30, 40, 41, 29, 42], [0, 1, 12, 16, 17, 30, 20, 43, 44, 45], [0, 1, 26, 12, 10, 16, 17, 46, 47, 48], [0, 5, 12, 1, 14, 49, 30, 50, 46, 51], [0, 52, 44, 53, 54, 1, 40, 30, 12, 55], [0, 44, 52, 53, 54, 1, 12, 30, 16, 43], [0, 1, 5, 16, 17, 14, 12, 43, 47, 24], [0, 16, 1, 17, 56, 12, 30, 5, 43, 57], [0, 16, 1, 43, 17, 58, 59, 12, 47, 5], [0, 1, 16, 12, 17, 26, 15, 4, 20, 5], [0, 1, 40, 5, 60, 4, 58, 2, 61, 57], [0, 1, 12, 5, 56, 48, 20, 4, 2, 3], [0, 12, 16, 1, 17, 39, 29, 5, 4, 20], [0, 16, 12, 17, 1, 62, 63, 19, 4, 64], [0, 12, 63, 62, 1, 16, 65, 17, 5, 2], [0

In [16]:
# generate a sequence of random numbers in [0, 99]
tweetIdsCount = -1
inputs = len(trendingTopicsAll)
trainAmount = int(inputs*0.6666)
testAmount = int(inputs*0.3333)


def generate_sequence():
    global tweetIdsCount
    print("tweetIdsCount - ",tweetIdsCount)
    tweetIdsCount = tweetIdsCount+1
    return (trendingIdsInEachDays[tweetIdsCount])
    #return [23,12,45]
    
# one hot encode sequence
def one_hot_encode(sequence, n_unique=inputs):
	encoding = list()
	for value in sequence:
		vector = [0 for _ in range(n_unique)]
		vector[value] = 1
		encoding.append(vector)  
	return numpy.array(encoding)
 
# decode a one hot encoded string
def one_hot_decode(encoded_seq):
	return [argmax(vector) for vector in encoded_seq]
 
# generate data for the lstm
def generate_data():
	# generate sequence
	sequence = generate_sequence()
	# one hot encode
	encoded = one_hot_encode(sequence)
	# convert to 3d for input
	X = encoded.reshape(encoded.shape[0], 1, encoded.shape[1])
	return X, encoded    
    
# define model
model = Sequential() 
model.add(LSTM(50, input_shape=(1, inputs)))
model.add(Dense(inputs, activation='relu'))
model.add(Dense(inputs, activation='softmax'))
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])
# fit model
for i in range(trainAmount):
	X, y = generate_data()
	model.fit(X, y, epochs=40, batch_size=1, verbose=2)
# evaluate model on new data
X, y = generate_data()
yhat = model.predict(X)

#print('Expected:  %s' % one_hot_decode(y))
#print('Predicted: %s' % one_hot_decode(yhat))

a = []
b = []
i = 0;
# for x in range(5):
#     if(one_hot_decode(y)[x] == one_hot_decode(yhat)[x]):
#         i += 1
#     a.append(trendingTopicsAll[one_hot_decode(y)[x]])
#     b.append(trendingTopicsAll[one_hot_decode(yhat)[x]])
   
# print("Expected: ",a)
# print("Predicted: ",b)
# print("Test Accuracy: ",(i/5)*100)

tweetIdsCount -  -1
Epoch 1/40
10/10 - 3s - loss: 8.0228 - acc: 0.0000e+00
Epoch 2/40
10/10 - 1s - loss: 7.9409 - acc: 0.1000
Epoch 3/40
10/10 - 1s - loss: 7.7478 - acc: 0.3000
Epoch 4/40
10/10 - 1s - loss: 7.2223 - acc: 0.1000
Epoch 5/40
10/10 - 1s - loss: 5.9989 - acc: 0.2000
Epoch 6/40
10/10 - 1s - loss: 3.7509 - acc: 0.1000
Epoch 7/40
10/10 - 1s - loss: 2.4703 - acc: 0.1000
Epoch 8/40
10/10 - 1s - loss: 2.3821 - acc: 0.0000e+00
Epoch 9/40
10/10 - 1s - loss: 2.3541 - acc: 0.0000e+00
Epoch 10/40
10/10 - 1s - loss: 2.3534 - acc: 0.1000
Epoch 11/40
10/10 - 1s - loss: 2.3262 - acc: 0.0000e+00
Epoch 12/40
10/10 - 1s - loss: 2.3198 - acc: 0.0000e+00
Epoch 13/40
10/10 - 1s - loss: 2.2690 - acc: 0.2000
Epoch 14/40
10/10 - 1s - loss: 2.2687 - acc: 0.1000
Epoch 15/40
10/10 - 1s - loss: 2.2145 - acc: 0.2000
Epoch 16/40
10/10 - 1s - loss: 2.1954 - acc: 0.2000
Epoch 17/40
10/10 - 1s - loss: 2.1511 - acc: 0.4000
Epoch 18/40
10/10 - 1s - loss: 2.1128 - acc: 0.8000
Epoch 19/40
10/10 - 1s - loss: 2.

Epoch 38/40
10/10 - 1s - loss: 0.0021 - acc: 1.0000
Epoch 39/40
10/10 - 1s - loss: 0.0019 - acc: 1.0000
Epoch 40/40
10/10 - 1s - loss: 0.0018 - acc: 1.0000
tweetIdsCount -  3
Epoch 1/40
10/10 - 1s - loss: 2.5968 - acc: 0.8000
Epoch 2/40
10/10 - 1s - loss: 1.4218 - acc: 0.8000
Epoch 3/40
10/10 - 1s - loss: 1.0506 - acc: 0.8000
Epoch 4/40
10/10 - 1s - loss: 0.5912 - acc: 0.8000
Epoch 5/40
10/10 - 1s - loss: 0.2453 - acc: 0.8000
Epoch 6/40
10/10 - 1s - loss: 0.1549 - acc: 0.9000
Epoch 7/40
10/10 - 1s - loss: 0.1501 - acc: 0.9000
Epoch 8/40
10/10 - 1s - loss: 0.1514 - acc: 0.9000
Epoch 9/40
10/10 - 1s - loss: 0.1076 - acc: 1.0000
Epoch 10/40
10/10 - 1s - loss: 0.0856 - acc: 1.0000
Epoch 11/40
10/10 - 1s - loss: 0.0512 - acc: 1.0000
Epoch 12/40
10/10 - 1s - loss: 0.0451 - acc: 1.0000
Epoch 13/40
10/10 - 1s - loss: 0.0230 - acc: 1.0000
Epoch 14/40
10/10 - 1s - loss: 0.0201 - acc: 1.0000
Epoch 15/40
10/10 - 1s - loss: 0.0116 - acc: 1.0000
Epoch 16/40
10/10 - 1s - loss: 0.0098 - acc: 1.0000
Ep

Epoch 35/40
10/10 - 1s - loss: 0.0019 - acc: 1.0000
Epoch 36/40
10/10 - 1s - loss: 0.0017 - acc: 1.0000
Epoch 37/40
10/10 - 1s - loss: 0.0016 - acc: 1.0000
Epoch 38/40
10/10 - 1s - loss: 0.0015 - acc: 1.0000
Epoch 39/40
10/10 - 1s - loss: 0.0014 - acc: 1.0000
Epoch 40/40
10/10 - 1s - loss: 0.0013 - acc: 1.0000
tweetIdsCount -  7
Epoch 1/40
10/10 - 1s - loss: 6.0008 - acc: 0.5000
Epoch 2/40
10/10 - 1s - loss: 3.5272 - acc: 0.5000
Epoch 3/40
10/10 - 1s - loss: 2.1858 - acc: 0.5000
Epoch 4/40
10/10 - 1s - loss: 1.0262 - acc: 0.5000
Epoch 5/40
10/10 - 1s - loss: 0.9259 - acc: 0.6000
Epoch 6/40
10/10 - 1s - loss: 0.8580 - acc: 0.6000
Epoch 7/40
10/10 - 1s - loss: 0.8138 - acc: 0.6000
Epoch 8/40
10/10 - 1s - loss: 0.6415 - acc: 0.7000
Epoch 9/40
10/10 - 1s - loss: 0.4982 - acc: 1.0000
Epoch 10/40
10/10 - 1s - loss: 0.4050 - acc: 1.0000
Epoch 11/40
10/10 - 1s - loss: 0.2756 - acc: 1.0000
Epoch 12/40
10/10 - 1s - loss: 0.1711 - acc: 1.0000
Epoch 13/40
10/10 - 1s - loss: 0.0916 - acc: 1.0000
Ep

Epoch 29/40
10/10 - 1s - loss: 0.0012 - acc: 1.0000
Epoch 30/40
10/10 - 1s - loss: 0.0011 - acc: 1.0000
Epoch 31/40
10/10 - 1s - loss: 0.0010 - acc: 1.0000
Epoch 32/40
10/10 - 1s - loss: 9.6608e-04 - acc: 1.0000
Epoch 33/40
10/10 - 1s - loss: 9.1452e-04 - acc: 1.0000
Epoch 34/40
10/10 - 1s - loss: 8.5048e-04 - acc: 1.0000
Epoch 35/40
10/10 - 1s - loss: 8.0900e-04 - acc: 1.0000
Epoch 36/40
10/10 - 1s - loss: 7.5801e-04 - acc: 1.0000
Epoch 37/40
10/10 - 1s - loss: 7.2006e-04 - acc: 1.0000
Epoch 38/40
10/10 - 1s - loss: 6.9037e-04 - acc: 1.0000
Epoch 39/40
10/10 - 1s - loss: 6.4975e-04 - acc: 1.0000
Epoch 40/40
10/10 - 1s - loss: 6.1628e-04 - acc: 1.0000
tweetIdsCount -  11
Epoch 1/40
10/10 - 1s - loss: 3.5880 - acc: 0.7000
Epoch 2/40
10/10 - 1s - loss: 2.3323 - acc: 0.7000
Epoch 3/40
10/10 - 1s - loss: 1.8199 - acc: 0.7000
Epoch 4/40
10/10 - 1s - loss: 1.1463 - acc: 0.7000
Epoch 5/40
10/10 - 1s - loss: 0.6395 - acc: 0.8000
Epoch 6/40
10/10 - 1s - loss: 0.3738 - acc: 0.8000
Epoch 7/40
10/

10/10 - 1s - loss: 0.0041 - acc: 1.0000
Epoch 25/40
10/10 - 1s - loss: 0.0036 - acc: 1.0000
Epoch 26/40
10/10 - 1s - loss: 0.0033 - acc: 1.0000
Epoch 27/40
10/10 - 1s - loss: 0.0028 - acc: 1.0000
Epoch 28/40
10/10 - 1s - loss: 0.0026 - acc: 1.0000
Epoch 29/40
10/10 - 1s - loss: 0.0024 - acc: 1.0000
Epoch 30/40
10/10 - 1s - loss: 0.0021 - acc: 1.0000
Epoch 31/40
10/10 - 1s - loss: 0.0020 - acc: 1.0000
Epoch 32/40
10/10 - 1s - loss: 0.0018 - acc: 1.0000
Epoch 33/40
10/10 - 1s - loss: 0.0017 - acc: 1.0000
Epoch 34/40
10/10 - 1s - loss: 0.0016 - acc: 1.0000
Epoch 35/40
10/10 - 1s - loss: 0.0015 - acc: 1.0000
Epoch 36/40
10/10 - 1s - loss: 0.0014 - acc: 1.0000
Epoch 37/40
10/10 - 1s - loss: 0.0013 - acc: 1.0000
Epoch 38/40
10/10 - 1s - loss: 0.0012 - acc: 1.0000
Epoch 39/40
10/10 - 1s - loss: 0.0011 - acc: 1.0000
Epoch 40/40
10/10 - 1s - loss: 0.0011 - acc: 1.0000
tweetIdsCount -  15
Epoch 1/40
10/10 - 1s - loss: 0.1336 - acc: 0.9000
Epoch 2/40
10/10 - 1s - loss: 0.0053 - acc: 1.0000
Epoch 

...

Epoch 19/40
10/10 - 1s - loss: 9.3217e-06 - acc: 1.0000
Epoch 20/40
10/10 - 1s - loss: 9.1906e-06 - acc: 1.0000
Epoch 21/40
10/10 - 1s - loss: 8.9999e-06 - acc: 1.0000
Epoch 22/40
10/10 - 1s - loss: 8.9880e-06 - acc: 1.0000
Epoch 23/40
10/10 - 1s - loss: 8.8330e-06 - acc: 1.0000
Epoch 24/40
10/10 - 1s - loss: 8.7853e-06 - acc: 1.0000
Epoch 25/40
10/10 - 1s - loss: 8.7257e-06 - acc: 1.0000
Epoch 26/40
10/10 - 1s - loss: 8.6781e-06 - acc: 1.0000
Epoch 27/40
10/10 - 1s - loss: 8.5350e-06 - acc: 1.0000
Epoch 28/40
10/10 - 1s - loss: 8.4516e-06 - acc: 1.0000
Epoch 29/40
10/10 - 1s - loss: 8.3205e-06 - acc: 1.0000
Epoch 30/40
10/10 - 1s - loss: 8.3562e-06 - acc: 1.0000
Epoch 31/40
10/10 - 1s - loss: 8.1893e-06 - acc: 1.0000
Epoch 32/40
10/10 - 1s - loss: 8.2013e-06 - acc: 1.0000
Epoch 33/40
10/10 - 1s - loss: 8.0582e-06 - acc: 1.0000
Epoch 34/40
10/10 - 1s - loss: 7.9867e-06 - acc: 1.0000
Epoch 35/40
10/10 - 1s - loss: 7.9390e-06 - acc: 1.0000
Epoch 36/40
10/10 - 1s - loss: 7.8556e-06 - acc:

Epoch 5/40
10/10 - 1s - loss: 3.2186e-07 - acc: 1.0000
Epoch 6/40
10/10 - 1s - loss: 3.0994e-07 - acc: 1.0000
Epoch 7/40
10/10 - 1s - loss: 3.0994e-07 - acc: 1.0000
Epoch 8/40
10/10 - 1s - loss: 2.9802e-07 - acc: 1.0000
Epoch 9/40
10/10 - 1s - loss: 2.9802e-07 - acc: 1.0000
Epoch 10/40
10/10 - 1s - loss: 2.9802e-07 - acc: 1.0000
Epoch 11/40
10/10 - 1s - loss: 2.9802e-07 - acc: 1.0000
Epoch 12/40
10/10 - 1s - loss: 2.8610e-07 - acc: 1.0000
Epoch 13/40
10/10 - 1s - loss: 2.8610e-07 - acc: 1.0000
Epoch 14/40
10/10 - 1s - loss: 2.8610e-07 - acc: 1.0000
Epoch 15/40
10/10 - 1s - loss: 2.7418e-07 - acc: 1.0000
Epoch 16/40
10/10 - 1s - loss: 2.7418e-07 - acc: 1.0000
Epoch 17/40
10/10 - 1s - loss: 2.6226e-07 - acc: 1.0000
Epoch 18/40
10/10 - 1s - loss: 2.6226e-07 - acc: 1.0000
Epoch 19/40
10/10 - 1s - loss: 2.6226e-07 - acc: 1.0000
Epoch 20/40
10/10 - 1s - loss: 2.5034e-07 - acc: 1.0000
Epoch 21/40
10/10 - 1s - loss: 2.5034e-07 - acc: 1.0000
Epoch 22/40
10/10 - 1s - loss: 2.5034e-07 - acc: 1.00

Epoch 31/40
10/10 - 1s - loss: 9.8943e-07 - acc: 1.0000
Epoch 32/40
10/10 - 1s - loss: 9.7751e-07 - acc: 1.0000
Epoch 33/40
10/10 - 1s - loss: 9.6559e-07 - acc: 1.0000
Epoch 34/40
10/10 - 1s - loss: 9.4175e-07 - acc: 1.0000
Epoch 35/40
10/10 - 1s - loss: 9.1791e-07 - acc: 1.0000
Epoch 36/40
10/10 - 1s - loss: 9.0599e-07 - acc: 1.0000
Epoch 37/40
10/10 - 1s - loss: 8.9407e-07 - acc: 1.0000
Epoch 38/40
10/10 - 1s - loss: 8.7022e-07 - acc: 1.0000
Epoch 39/40
10/10 - 1s - loss: 8.7022e-07 - acc: 1.0000
Epoch 40/40
10/10 - 1s - loss: 8.4638e-07 - acc: 1.0000
tweetIdsCount -  2021
Epoch 1/40
10/10 - 1s - loss: 9.2983e-07 - acc: 1.0000
Epoch 2/40
10/10 - 1s - loss: 9.1791e-07 - acc: 1.0000
Epoch 3/40
10/10 - 1s - loss: 9.0599e-07 - acc: 1.0000
Epoch 4/40
10/10 - 1s - loss: 8.9407e-07 - acc: 1.0000
Epoch 5/40
10/10 - 1s - loss: 8.8215e-07 - acc: 1.0000
Epoch 6/40
10/10 - 1s - loss: 8.5830e-07 - acc: 1.0000
Epoch 7/40
10/10 - 1s - loss: 8.4638e-07 - acc: 1.0000
Epoch 8/40
10/10 - 1s - loss: 8.2

Epoch 20/40
10/10 - 1s - loss: 0.0024 - acc: 1.0000
Epoch 21/40
10/10 - 1s - loss: 0.0022 - acc: 1.0000
Epoch 22/40
10/10 - 1s - loss: 0.0020 - acc: 1.0000
Epoch 23/40
10/10 - 1s - loss: 0.0019 - acc: 1.0000
Epoch 24/40
10/10 - 1s - loss: 0.0018 - acc: 1.0000
Epoch 25/40
10/10 - 1s - loss: 0.0016 - acc: 1.0000
Epoch 26/40
10/10 - 1s - loss: 0.0015 - acc: 1.0000
Epoch 27/40
10/10 - 1s - loss: 0.0014 - acc: 1.0000
Epoch 28/40
10/10 - 1s - loss: 0.0014 - acc: 1.0000
Epoch 29/40
10/10 - 1s - loss: 0.0013 - acc: 1.0000
Epoch 30/40
10/10 - 1s - loss: 0.0012 - acc: 1.0000
Epoch 31/40
10/10 - 1s - loss: 0.0011 - acc: 1.0000
Epoch 32/40
10/10 - 1s - loss: 0.0011 - acc: 1.0000
Epoch 33/40
10/10 - 1s - loss: 0.0010 - acc: 1.0000
Epoch 34/40
10/10 - 1s - loss: 9.5485e-04 - acc: 1.0000
Epoch 35/40
10/10 - 1s - loss: 9.0067e-04 - acc: 1.0000
Epoch 36/40
10/10 - 1s - loss: 8.6725e-04 - acc: 1.0000
Epoch 37/40
10/10 - 1s - loss: 8.2176e-04 - acc: 1.0000
Epoch 38/40
10/10 - 1s - loss: 7.7745e-04 - acc:

Epoch 11/40
10/10 - 1s - loss: 2.9524e-05 - acc: 1.0000
Epoch 12/40
10/10 - 1s - loss: 2.9047e-05 - acc: 1.0000
Epoch 13/40
10/10 - 1s - loss: 2.8582e-05 - acc: 1.0000
Epoch 14/40
10/10 - 1s - loss: 2.8427e-05 - acc: 1.0000
Epoch 15/40
10/10 - 1s - loss: 2.8094e-05 - acc: 1.0000
Epoch 16/40
10/10 - 1s - loss: 2.7820e-05 - acc: 1.0000
Epoch 17/40
10/10 - 1s - loss: 2.7677e-05 - acc: 1.0000
Epoch 18/40
10/10 - 1s - loss: 2.7283e-05 - acc: 1.0000
Epoch 19/40
10/10 - 1s - loss: 2.7176e-05 - acc: 1.0000
Epoch 20/40
10/10 - 1s - loss: 2.7105e-05 - acc: 1.0000
Epoch 21/40
10/10 - 1s - loss: 2.6687e-05 - acc: 1.0000
Epoch 22/40
10/10 - 1s - loss: 2.6366e-05 - acc: 1.0000
Epoch 23/40
10/10 - 1s - loss: 2.6235e-05 - acc: 1.0000
Epoch 24/40
10/10 - 1s - loss: 2.6187e-05 - acc: 1.0000
Epoch 25/40
10/10 - 1s - loss: 2.5960e-05 - acc: 1.0000
Epoch 26/40
10/10 - 1s - loss: 2.5663e-05 - acc: 1.0000
Epoch 27/40
10/10 - 1s - loss: 2.5520e-05 - acc: 1.0000
Epoch 28/40
10/10 - 1s - loss: 2.5114e-05 - acc:

In [17]:
model_json = model.to_json()
with open("model.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
model.save_weights("final.h5")
print("Saved model to disk")

Saved model to disk


In [18]:
print(tweetIdsCount)
testaccuracy = []

def getOneAccuracy(a,b):
    i = 0;
    for x in range(10):
        if(a[x] == b[x]):
            i += 1
    return i/10

def getTestData():
    for i in range(testAmount):
        X, y = generate_data()
        yhat = model.predict(X)
        print('Expected:  %s' % one_hot_decode(y))
        print('Predicted: %s' % one_hot_decode(yhat))
        testaccuracy.append(getOneAccuracy(one_hot_decode(y),one_hot_decode(yhat)))
    
getTestData()
print(testaccuracy)
print('average - ',sum(testaccuracy) / len(testaccuracy))

2031
tweetIdsCount -  2031
Expected:  [0, 117, 204, 1255, 224, 716, 865, 2464, 2499, 1140]
Predicted: [0, 117, 204, 1255, 224, 716, 865, 2464, 2499, 1140]
tweetIdsCount -  2032
Expected:  [0, 117, 204, 1255, 865, 224, 1140, 1298, 716, 2464]
Predicted: [0, 117, 204, 1255, 865, 224, 1140, 1298, 716, 2464]
tweetIdsCount -  2033
Expected:  [0, 204, 865, 1255, 1140, 1298, 224, 2499, 117, 716]
Predicted: [0, 204, 865, 1255, 1140, 1298, 224, 2499, 117, 716]
tweetIdsCount -  2034
Expected:  [204, 117, 865, 1298, 716, 1255, 2464, 2499, 1140, 224]
Predicted: [204, 117, 865, 1298, 716, 1255, 2464, 2499, 1140, 224]
tweetIdsCount -  2035
Expected:  [0, 50, 783, 291, 280, 1396, 2500, 191, 2501, 2502]
Predicted: [0, 50, 783, 291, 280, 2499, 2499, 191, 2499, 2499]
tweetIdsCount -  2036
Expected:  [0, 117, 204, 224, 1255, 1298, 716, 865, 1140, 2464]
Predicted: [0, 117, 204, 224, 1255, 1298, 716, 865, 1140, 2464]
tweetIdsCount -  2037
Expected:  [0, 117, 204, 1298, 1255, 716, 224, 865, 2464, 2499]
Predi

Expected:  [0, 224, 117, 204, 716, 1255, 865, 1298, 2464, 2499]
Predicted: [0, 224, 117, 204, 716, 1255, 865, 1298, 2464, 2499]
tweetIdsCount -  2089
Expected:  [0, 224, 117, 204, 1140, 1255, 716, 865, 2464, 2499]
Predicted: [0, 224, 117, 204, 1140, 1255, 716, 865, 2464, 2499]
tweetIdsCount -  2090
Expected:  [0, 2520, 329, 50, 2444, 16, 2521, 280, 679, 2449]
Predicted: [0, 2499, 329, 50, 2444, 16, 2499, 280, 679, 2449]
tweetIdsCount -  2091
Expected:  [0, 117, 204, 2499, 224, 716, 1255, 865, 1298, 2464]
Predicted: [0, 117, 204, 2499, 224, 716, 1255, 865, 1298, 2464]
tweetIdsCount -  2092
Expected:  [0, 1, 2522, 28, 280, 1606, 679, 2523, 525, 2449]
Predicted: [0, 1, 1298, 28, 280, 1606, 679, 2499, 525, 2449]
tweetIdsCount -  2093
Expected:  [0, 204, 1298, 117, 1255, 716, 224, 2445, 865, 2464]
Predicted: [0, 204, 1298, 117, 1255, 716, 224, 2445, 865, 2464]
tweetIdsCount -  2094
Expected:  [0, 2524, 329, 50, 2444, 2445, 1, 48, 182, 2449]
Predicted: [0, 2499, 329, 50, 2444, 2445, 1, 48, 1

Expected:  [0, 2563, 2445, 1, 2551, 329, 50, 839, 679, 16]
Predicted: [0, 2499, 2445, 1, 2499, 329, 50, 839, 679, 16]
tweetIdsCount -  2147
Expected:  [0, 615, 564, 329, 50, 2444, 2445, 280, 1274, 1]
Predicted: [0, 615, 564, 329, 50, 2444, 2445, 280, 1274, 1]
tweetIdsCount -  2148
Expected:  [0, 329, 50, 2444, 2564, 1, 2565, 518, 2566, 2567]
Predicted: [0, 329, 50, 2444, 2499, 1, 2499, 2499, 287, 2499]
tweetIdsCount -  2149
Expected:  [0, 2445, 329, 50, 2551, 2444, 1, 998, 48, 132]
Predicted: [0, 2445, 329, 50, 2499, 2444, 1, 998, 48, 132]
tweetIdsCount -  2150
Expected:  [0, 2445, 329, 280, 50, 2444, 2551, 48, 679, 1924]
Predicted: [0, 2445, 329, 280, 50, 2444, 2499, 48, 679, 1924]
tweetIdsCount -  2151
Expected:  [0, 2568, 329, 50, 2444, 1274, 1, 280, 679, 48]
Predicted: [0, 2499, 329, 50, 2444, 1274, 1, 280, 679, 48]
tweetIdsCount -  2152
Expected:  [0, 2569, 1, 329, 50, 2444, 2570, 2567, 16, 679]
Predicted: [0, 2499, 1, 329, 50, 2444, 2499, 2499, 16, 679]
tweetIdsCount -  2153
Expe

Expected:  [0, 129, 2623, 2624, 50, 2445, 934, 1, 2444, 48]
Predicted: [0, 129, 2499, 2499, 50, 2445, 1215, 1, 2444, 48]
tweetIdsCount -  2208
Expected:  [0, 2625, 2445, 2623, 1, 2626, 2627, 2628, 2624, 48]
Predicted: [0, 2499, 2445, 2499, 1, 1298, 2499, 2499, 2499, 48]
tweetIdsCount -  2209
Expected:  [0, 50, 934, 2444, 2623, 2629, 7, 2624, 2630, 2631]
Predicted: [0, 50, 1215, 2444, 2499, 2499, 7, 2499, 2499, 2499]
tweetIdsCount -  2210
Expected:  [0, 679, 998, 48, 100, 50, 1606, 1, 1924, 11]
Predicted: [0, 679, 998, 48, 100, 50, 1606, 1, 1924, 11]
tweetIdsCount -  2211
Expected:  [0, 2445, 48, 679, 1924, 998, 1606, 1746, 526, 1]
Predicted: [0, 2445, 48, 679, 1924, 998, 1606, 1746, 526, 1]
tweetIdsCount -  2212
Expected:  [0, 2623, 261, 2624, 50, 1, 934, 2444, 1924, 679]
Predicted: [0, 2499, 261, 2499, 50, 1, 1215, 2444, 1924, 679]
tweetIdsCount -  2213
Expected:  [0, 580, 19, 50, 100, 1, 2444, 2445, 934, 998]
Predicted: [0, 2499, 19, 50, 100, 1, 2444, 2445, 1215, 998]
tweetIdsCount -

Expected:  [0, 2624, 2645, 1, 679, 2445, 2449, 48, 329, 280]
Predicted: [0, 2499, 2499, 1, 679, 2445, 2449, 48, 329, 280]
tweetIdsCount -  2269
Expected:  [0, 2445, 2677, 1, 48, 2449, 16, 50, 679, 1746]
Predicted: [0, 2445, 2499, 1, 48, 2449, 16, 50, 679, 1746]
tweetIdsCount -  2270
Expected:  [0, 129, 2624, 2623, 2445, 2678, 1, 2679, 2449, 50]
Predicted: [0, 129, 2499, 2499, 2445, 2499, 1, 2499, 2449, 50]
tweetIdsCount -  2271
Expected:  [0, 2445, 129, 48, 2624, 2623, 2449, 1924, 1, 2680]
Predicted: [0, 2445, 129, 48, 2499, 2499, 2449, 1924, 1, 2499]
tweetIdsCount -  2272
Expected:  [0, 2445, 48, 1, 2449, 2663, 2664, 679, 1924, 526]
Predicted: [0, 2445, 48, 1, 2449, 1298, 1298, 679, 1924, 526]
tweetIdsCount -  2273
Expected:  [0, 2445, 232, 2672, 2623, 2624, 1, 23, 28, 48]
Predicted: [0, 2445, 232, 2499, 2499, 2499, 1, 23, 28, 48]
tweetIdsCount -  2274
Expected:  [0, 2445, 329, 1, 19, 48, 16, 2449, 280, 679]
Predicted: [0, 2445, 329, 1, 19, 48, 16, 2449, 280, 679]
tweetIdsCount -  227

...

Expected:  [0, 48, 679, 11, 998, 525, 1689, 1746, 2154, 1916]
Predicted: [0, 48, 679, 11, 998, 525, 1689, 1746, 2154, 1399]
tweetIdsCount -  2803
Expected:  [0, 48, 998, 679, 1689, 11, 1746, 113, 525, 2154]
Predicted: [0, 48, 998, 679, 1689, 11, 1746, 113, 525, 2154]
tweetIdsCount -  2804
Expected:  [0, 48, 679, 998, 11, 2956, 2154, 1746, 1689, 525]
Predicted: [0, 48, 679, 998, 11, 2499, 2154, 1746, 1689, 525]
tweetIdsCount -  2805
Expected:  [0, 679, 1916, 48, 1746, 998, 11, 525, 280, 1689]
Predicted: [0, 679, 1399, 48, 1746, 998, 11, 525, 280, 1689]
tweetIdsCount -  2806
Expected:  [0, 679, 11, 48, 998, 1746, 1689, 525, 1916, 1606]
Predicted: [0, 679, 11, 48, 998, 1746, 1689, 525, 1399, 1606]
tweetIdsCount -  2807
Expected:  [0, 48, 11, 679, 1746, 998, 1689, 525, 2901, 1606]
Predicted: [0, 48, 11, 679, 1746, 998, 1689, 525, 2499, 1606]
tweetIdsCount -  2808
Expected:  [0, 48, 679, 11, 998, 525, 1746, 1689, 2154, 738]
Predicted: [0, 48, 679, 11, 998, 525, 1746, 1689, 2154, 738]
tweetI

Expected:  [0, 48, 11, 679, 998, 112, 525, 28, 1, 783]
Predicted: [0, 48, 11, 679, 998, 112, 525, 28, 1, 783]
tweetIdsCount -  2864
Expected:  [0, 48, 11, 679, 998, 1746, 783, 1, 525, 132]
Predicted: [0, 48, 11, 679, 998, 1746, 783, 1, 525, 132]
tweetIdsCount -  2865
Expected:  [0, 48, 11, 998, 679, 525, 287, 1746, 2970, 1689]
Predicted: [0, 48, 11, 998, 679, 525, 287, 1746, 1298, 1689]
tweetIdsCount -  2866
Expected:  [0, 48, 679, 11, 998, 132, 1916, 2971, 525, 2965]
Predicted: [0, 48, 679, 11, 998, 132, 1399, 2499, 525, 1298]
tweetIdsCount -  2867
Expected:  [0, 48, 679, 11, 998, 1746, 280, 1689, 132, 1812]
Predicted: [0, 48, 679, 11, 998, 1746, 280, 1689, 132, 1812]
tweetIdsCount -  2868
Expected:  [0, 48, 679, 11, 998, 525, 1689, 1746, 2972, 1]
Predicted: [0, 48, 679, 11, 998, 525, 1689, 1746, 2499, 1]
tweetIdsCount -  2869
Expected:  [0, 48, 11, 679, 998, 112, 280, 1924, 525, 1746]
Predicted: [0, 48, 11, 679, 998, 112, 280, 1924, 525, 1746]
tweetIdsCount -  2870
Expected:  [0, 48,

Expected:  [0, 48, 679, 11, 525, 256, 998, 1689, 1746, 1]
Predicted: [0, 48, 679, 11, 525, 256, 998, 1689, 1746, 1]
tweetIdsCount -  2923
Expected:  [0, 48, 679, 2987, 256, 280, 1, 1689, 112, 2784]
Predicted: [0, 48, 679, 2499, 256, 280, 1, 1689, 112, 1854]
tweetIdsCount -  2924
Expected:  [0, 48, 679, 280, 1, 256, 1689, 525, 2784, 11]
Predicted: [0, 48, 679, 280, 1, 256, 1689, 525, 1854, 11]
tweetIdsCount -  2925
Expected:  [0, 48, 679, 1689, 998, 11, 2784, 280, 525, 256]
Predicted: [0, 48, 679, 1689, 998, 11, 1854, 280, 525, 256]
tweetIdsCount -  2926
Expected:  [0, 48, 679, 1689, 525, 2784, 256, 11, 280, 998]
Predicted: [0, 48, 679, 1689, 525, 1854, 256, 11, 280, 998]
tweetIdsCount -  2927
Expected:  [0, 48, 679, 1689, 998, 11, 525, 1746, 256, 2784]
Predicted: [0, 48, 679, 1689, 998, 11, 525, 1746, 256, 1854]
tweetIdsCount -  2928
Expected:  [0, 48, 679, 1689, 11, 749, 998, 112, 256, 525]
Predicted: [0, 48, 679, 1689, 11, 1303, 998, 112, 256, 525]
tweetIdsCount -  2929
Expected:  [0

Expected:  [0, 48, 679, 11, 998, 525, 1689, 2818, 2784, 1746]
Predicted: [0, 48, 679, 11, 998, 525, 1689, 2499, 1854, 1746]
tweetIdsCount -  2985
Expected:  [0, 48, 679, 11, 998, 525, 1689, 2818, 256, 1]
Predicted: [0, 48, 679, 11, 998, 525, 1689, 2499, 256, 1]
tweetIdsCount -  2986
Expected:  [0, 48, 679, 11, 1689, 998, 525, 268, 1746, 2818]
Predicted: [0, 48, 679, 11, 1689, 998, 525, 2499, 1746, 2499]
tweetIdsCount -  2987
Expected:  [0, 48, 679, 11, 525, 1689, 1, 2818, 998, 256]
Predicted: [0, 48, 679, 11, 525, 1689, 1, 2499, 998, 256]
tweetIdsCount -  2988
Expected:  [0, 48, 679, 11, 1689, 525, 998, 1, 1746, 2154]
Predicted: [0, 48, 679, 11, 1689, 525, 998, 1, 1746, 2154]
tweetIdsCount -  2989
Expected:  [0, 48, 679, 1689, 11, 525, 998, 2818, 1924, 2784]
Predicted: [0, 48, 679, 1689, 11, 525, 998, 2499, 1924, 1854]
tweetIdsCount -  2990
Expected:  [0, 48, 679, 11, 1689, 1, 525, 998, 112, 280]
Predicted: [0, 48, 679, 11, 1689, 1, 525, 998, 112, 280]
tweetIdsCount -  2991
Expected:  

Expected:  [0, 48, 11, 679, 998, 1689, 525, 1746, 1, 2154]
Predicted: [0, 48, 11, 679, 998, 1689, 525, 1746, 1, 2154]
tweetIdsCount -  3044
Expected:  [0, 48, 1, 11, 679, 112, 1155, 998, 190, 1746]
Predicted: [0, 48, 1, 11, 679, 112, 1298, 998, 190, 1746]
tweetIdsCount -  3045
Expected:  [0, 48, 1, 11, 679, 112, 1746, 998, 190, 1155]
Predicted: [0, 48, 1, 11, 679, 112, 1746, 998, 190, 1298]
[1.0, 1.0, 1.0, 1.0, 0.6, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.8, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9, 0.8, 0.7, 0.8, 0.9, 1.0, 0.8, 1.0, 1.0, 0.8, 0.9, 1.0, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 1.0, 0.8, 1.0, 1.0, 1.0, 0.8, 1.0, 0.9, 0.9, 1.0, 1.0, 0.8, 1.0, 0.8, 1.0, 0.9, 1.0, 1.0, 0.9, 0.9, 1.0, 1.0, 0.8, 1.0, 1.0, 0.7, 0.8, 1.0, 1.0, 1.0, 0.3, 1.0, 0.9, 1.0, 1.0, 0.9, 1.0, 0.8, 1.0, 1.0, 1.0, 0.9, 1.0, 1.0, 0.9, 0.8, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 1.0, 0.8, 0.5, 0.8, 0.8, 0.8, 0.8, 0.7, 0.8, 0.8, 0.8, 0.8, 0.8, 0.5, 0.7, 0.8, 1.0, 0.5, 0.9, 0.9, 0.9, 

In [19]:
tweetIdsCount = 2031
print(tweetIdsCount)
testaccuracy = []

def getOneAccuracy(a,b):
    i = 0;
    for x in range(10):
        if(a[x] == b[x]):
            i += 1
    return i/10

def getTestData():
    for i in range(testAmount):
        X, y = generate_data()
        yhat = model.predict(X)
        print('Expected:  %s' % one_hot_decode(y))
        print('Predicted: %s' % one_hot_decode(yhat))
        testaccuracy.append(getOneAccuracy(one_hot_decode(y),one_hot_decode(yhat)))
    
getTestData()
print(testaccuracy)
print('accuracy - ',sum(testaccuracy) / len(testaccuracy))

2031
tweetIdsCount -  2031
Expected:  [0, 117, 204, 1255, 224, 716, 865, 2464, 2499, 1140]
Predicted: [0, 117, 204, 1255, 224, 716, 865, 2464, 2499, 1140]
tweetIdsCount -  2032
Expected:  [0, 117, 204, 1255, 865, 224, 1140, 1298, 716, 2464]
Predicted: [0, 117, 204, 1255, 865, 224, 1140, 1298, 716, 2464]
tweetIdsCount -  2033
Expected:  [0, 204, 865, 1255, 1140, 1298, 224, 2499, 117, 716]
Predicted: [0, 204, 865, 1255, 1140, 1298, 224, 2499, 117, 716]
tweetIdsCount -  2034
Expected:  [204, 117, 865, 1298, 716, 1255, 2464, 2499, 1140, 224]
Predicted: [204, 117, 865, 1298, 716, 1255, 2464, 2499, 1140, 224]
tweetIdsCount -  2035
Expected:  [0, 50, 783, 291, 280, 1396, 2500, 191, 2501, 2502]
Predicted: [0, 50, 783, 291, 280, 2499, 2499, 191, 2499, 2499]
tweetIdsCount -  2036
Expected:  [0, 117, 204, 224, 1255, 1298, 716, 865, 1140, 2464]
Predicted: [0, 117, 204, 224, 1255, 1298, 716, 865, 1140, 2464]
tweetIdsCount -  2037
Expected:  [0, 117, 204, 1298, 1255, 716, 224, 865, 2464, 2499]
Predi

Expected:  [0, 2519, 204, 1255, 117, 2499, 1298, 716, 1140, 865]
Predicted: [0, 2499, 204, 1255, 117, 2499, 1298, 716, 1140, 865]
tweetIdsCount -  2088
Expected:  [0, 224, 117, 204, 716, 1255, 865, 1298, 2464, 2499]
Predicted: [0, 224, 117, 204, 716, 1255, 865, 1298, 2464, 2499]
tweetIdsCount -  2089
Expected:  [0, 224, 117, 204, 1140, 1255, 716, 865, 2464, 2499]
Predicted: [0, 224, 117, 204, 1140, 1255, 716, 865, 2464, 2499]
tweetIdsCount -  2090
Expected:  [0, 2520, 329, 50, 2444, 16, 2521, 280, 679, 2449]
Predicted: [0, 2499, 329, 50, 2444, 16, 2499, 280, 679, 2449]
tweetIdsCount -  2091
Expected:  [0, 117, 204, 2499, 224, 716, 1255, 865, 1298, 2464]
Predicted: [0, 117, 204, 2499, 224, 716, 1255, 865, 1298, 2464]
tweetIdsCount -  2092
Expected:  [0, 1, 2522, 28, 280, 1606, 679, 2523, 525, 2449]
Predicted: [0, 1, 1298, 28, 280, 1606, 679, 2499, 525, 2449]
tweetIdsCount -  2093
Expected:  [0, 204, 1298, 117, 1255, 716, 224, 2445, 865, 2464]
Predicted: [0, 204, 1298, 117, 1255, 716, 22

Expected:  [0, 615, 564, 329, 50, 2444, 2445, 280, 1274, 1]
Predicted: [0, 615, 564, 329, 50, 2444, 2445, 280, 1274, 1]
tweetIdsCount -  2148
Expected:  [0, 329, 50, 2444, 2564, 1, 2565, 518, 2566, 2567]
Predicted: [0, 329, 50, 2444, 2499, 1, 2499, 2499, 287, 2499]
tweetIdsCount -  2149
Expected:  [0, 2445, 329, 50, 2551, 2444, 1, 998, 48, 132]
Predicted: [0, 2445, 329, 50, 2499, 2444, 1, 998, 48, 132]
tweetIdsCount -  2150
Expected:  [0, 2445, 329, 280, 50, 2444, 2551, 48, 679, 1924]
Predicted: [0, 2445, 329, 280, 50, 2444, 2499, 48, 679, 1924]
tweetIdsCount -  2151
Expected:  [0, 2568, 329, 50, 2444, 1274, 1, 280, 679, 48]
Predicted: [0, 2499, 329, 50, 2444, 1274, 1, 280, 679, 48]
tweetIdsCount -  2152
Expected:  [0, 2569, 1, 329, 50, 2444, 2570, 2567, 16, 679]
Predicted: [0, 2499, 1, 329, 50, 2444, 2499, 2499, 16, 679]
tweetIdsCount -  2153
Expected:  [2571, 0, 2569, 50, 329, 2445, 2444, 1, 2572, 48]
Predicted: [1298, 0, 2499, 50, 329, 2445, 2444, 1, 2499, 48]
tweetIdsCount -  2154


Expected:  [0, 2445, 50, 1, 934, 2444, 19, 2605, 48, 448]
Predicted: [0, 2445, 50, 1, 1215, 2444, 19, 2499, 48, 129]
tweetIdsCount -  2207
Expected:  [0, 129, 2623, 2624, 50, 2445, 934, 1, 2444, 48]
Predicted: [0, 129, 2499, 2499, 50, 2445, 1215, 1, 2444, 48]
tweetIdsCount -  2208
Expected:  [0, 2625, 2445, 2623, 1, 2626, 2627, 2628, 2624, 48]
Predicted: [0, 2499, 2445, 2499, 1, 1298, 2499, 2499, 2499, 48]
tweetIdsCount -  2209
Expected:  [0, 50, 934, 2444, 2623, 2629, 7, 2624, 2630, 2631]
Predicted: [0, 50, 1215, 2444, 2499, 2499, 7, 2499, 2499, 2499]
tweetIdsCount -  2210
Expected:  [0, 679, 998, 48, 100, 50, 1606, 1, 1924, 11]
Predicted: [0, 679, 998, 48, 100, 50, 1606, 1, 1924, 11]
tweetIdsCount -  2211
Expected:  [0, 2445, 48, 679, 1924, 998, 1606, 1746, 526, 1]
Predicted: [0, 2445, 48, 679, 1924, 998, 1606, 1746, 526, 1]
tweetIdsCount -  2212
Expected:  [0, 2623, 261, 2624, 50, 1, 934, 2444, 1924, 679]
Predicted: [0, 2499, 261, 2499, 50, 1, 1215, 2444, 1924, 679]
tweetIdsCount - 

Expected:  [0, 266, 998, 16, 1924, 1, 287, 2673, 2671, 679]
Predicted: [0, 266, 998, 16, 1924, 1, 287, 2499, 2499, 679]
tweetIdsCount -  2265
Expected:  [0, 2445, 1924, 280, 2663, 2664, 679, 1606, 48, 2449]
Predicted: [0, 2445, 1924, 280, 1298, 1298, 679, 1606, 48, 2449]
tweetIdsCount -  2266
Expected:  [0, 2623, 2624, 261, 2674, 679, 1, 48, 280, 1924]
Predicted: [0, 2499, 2499, 261, 2499, 679, 1, 48, 280, 1924]
tweetIdsCount -  2267
Expected:  [0, 2675, 266, 2676, 679, 1746, 19, 1606, 1924, 1812]
Predicted: [0, 2499, 266, 2499, 679, 1746, 19, 1606, 1924, 1812]
tweetIdsCount -  2268
Expected:  [0, 2624, 2645, 1, 679, 2445, 2449, 48, 329, 280]
Predicted: [0, 2499, 2499, 1, 679, 2445, 2449, 48, 329, 280]
tweetIdsCount -  2269
Expected:  [0, 2445, 2677, 1, 48, 2449, 16, 50, 679, 1746]
Predicted: [0, 2445, 2499, 1, 48, 2449, 16, 50, 679, 1746]
tweetIdsCount -  2270
Expected:  [0, 129, 2624, 2623, 2445, 2678, 1, 2679, 2449, 50]
Predicted: [0, 129, 2499, 2499, 2445, 2499, 1, 2499, 2449, 50]


...

Expected:  [0, 679, 11, 48, 998, 1746, 1689, 525, 1916, 1606]
Predicted: [0, 679, 11, 48, 998, 1746, 1689, 525, 1399, 1606]
tweetIdsCount -  2807
Expected:  [0, 48, 11, 679, 1746, 998, 1689, 525, 2901, 1606]
Predicted: [0, 48, 11, 679, 1746, 998, 1689, 525, 2499, 1606]
tweetIdsCount -  2808
Expected:  [0, 48, 679, 11, 998, 525, 1746, 1689, 2154, 738]
Predicted: [0, 48, 679, 11, 998, 525, 1746, 1689, 2154, 738]
tweetIdsCount -  2809
Expected:  [0, 679, 1746, 48, 11, 525, 998, 1689, 2154, 2486]
Predicted: [0, 679, 1746, 48, 11, 525, 998, 1689, 2154, 2486]
tweetIdsCount -  2810
Expected:  [0, 48, 679, 11, 525, 1746, 998, 1689, 2154, 738]
Predicted: [0, 48, 679, 11, 525, 1746, 998, 1689, 2154, 738]
tweetIdsCount -  2811
Expected:  [0, 48, 11, 679, 998, 525, 2901, 1746, 2957, 1924]
Predicted: [0, 48, 11, 679, 998, 525, 2499, 1746, 1854, 1924]
tweetIdsCount -  2812
Expected:  [0, 1746, 48, 998, 679, 525, 11, 1606, 1689, 1044]
Predicted: [0, 1746, 48, 998, 679, 525, 11, 1606, 1689, 1044]
twee

Expected:  [0, 48, 11, 998, 679, 525, 287, 1746, 2970, 1689]
Predicted: [0, 48, 11, 998, 679, 525, 287, 1746, 1298, 1689]
tweetIdsCount -  2866
Expected:  [0, 48, 679, 11, 998, 132, 1916, 2971, 525, 2965]
Predicted: [0, 48, 679, 11, 998, 132, 1399, 2499, 525, 1298]
tweetIdsCount -  2867
Expected:  [0, 48, 679, 11, 998, 1746, 280, 1689, 132, 1812]
Predicted: [0, 48, 679, 11, 998, 1746, 280, 1689, 132, 1812]
tweetIdsCount -  2868
Expected:  [0, 48, 679, 11, 998, 525, 1689, 1746, 2972, 1]
Predicted: [0, 48, 679, 11, 998, 525, 1689, 1746, 2499, 1]
tweetIdsCount -  2869
Expected:  [0, 48, 11, 679, 998, 112, 280, 1924, 525, 1746]
Predicted: [0, 48, 11, 679, 998, 112, 280, 1924, 525, 1746]
tweetIdsCount -  2870
Expected:  [0, 48, 100, 679, 11, 1916, 280, 998, 525, 2956]
Predicted: [0, 48, 100, 679, 11, 1399, 280, 998, 525, 2499]
tweetIdsCount -  2871
Expected:  [0, 48, 679, 11, 998, 1746, 525, 1689, 1606, 1924]
Predicted: [0, 48, 679, 11, 998, 1746, 525, 1689, 1606, 1924]
tweetIdsCount -  287

Expected:  [0, 48, 679, 2987, 256, 280, 1, 1689, 112, 2784]
Predicted: [0, 48, 679, 2499, 256, 280, 1, 1689, 112, 1854]
tweetIdsCount -  2924
Expected:  [0, 48, 679, 280, 1, 256, 1689, 525, 2784, 11]
Predicted: [0, 48, 679, 280, 1, 256, 1689, 525, 1854, 11]
tweetIdsCount -  2925
Expected:  [0, 48, 679, 1689, 998, 11, 2784, 280, 525, 256]
Predicted: [0, 48, 679, 1689, 998, 11, 1854, 280, 525, 256]
tweetIdsCount -  2926
Expected:  [0, 48, 679, 1689, 525, 2784, 256, 11, 280, 998]
Predicted: [0, 48, 679, 1689, 525, 1854, 256, 11, 280, 998]
tweetIdsCount -  2927
Expected:  [0, 48, 679, 1689, 998, 11, 525, 1746, 256, 2784]
Predicted: [0, 48, 679, 1689, 998, 11, 525, 1746, 256, 1854]
tweetIdsCount -  2928
Expected:  [0, 48, 679, 1689, 11, 749, 998, 112, 256, 525]
Predicted: [0, 48, 679, 1689, 11, 1303, 998, 112, 256, 525]
tweetIdsCount -  2929
Expected:  [0, 48, 679, 1175, 256, 1, 280, 1689, 525, 2784]
Predicted: [0, 48, 679, 1175, 256, 1, 280, 1689, 525, 1854]
tweetIdsCount -  2930
Expected:

Expected:  [0, 48, 679, 11, 1689, 525, 998, 1746, 1, 1155]
Predicted: [0, 48, 679, 11, 1689, 525, 998, 1746, 1, 1298]
tweetIdsCount -  2984
Expected:  [0, 48, 679, 11, 998, 525, 1689, 2818, 2784, 1746]
Predicted: [0, 48, 679, 11, 998, 525, 1689, 2499, 1854, 1746]
tweetIdsCount -  2985
Expected:  [0, 48, 679, 11, 998, 525, 1689, 2818, 256, 1]
Predicted: [0, 48, 679, 11, 998, 525, 1689, 2499, 256, 1]
tweetIdsCount -  2986
Expected:  [0, 48, 679, 11, 1689, 998, 525, 268, 1746, 2818]
Predicted: [0, 48, 679, 11, 1689, 998, 525, 2499, 1746, 2499]
tweetIdsCount -  2987
Expected:  [0, 48, 679, 11, 525, 1689, 1, 2818, 998, 256]
Predicted: [0, 48, 679, 11, 525, 1689, 1, 2499, 998, 256]
tweetIdsCount -  2988
Expected:  [0, 48, 679, 11, 1689, 525, 998, 1, 1746, 2154]
Predicted: [0, 48, 679, 11, 1689, 525, 998, 1, 1746, 2154]
tweetIdsCount -  2989
Expected:  [0, 48, 679, 1689, 11, 525, 998, 2818, 1924, 2784]
Predicted: [0, 48, 679, 1689, 11, 525, 998, 2499, 1924, 1854]
tweetIdsCount -  2990
Expecte

Predicted: [0, 48, 11, 679, 998, 1689, 525, 1746, 1, 2154]
tweetIdsCount -  3044
Expected:  [0, 48, 1, 11, 679, 112, 1155, 998, 190, 1746]
Predicted: [0, 48, 1, 11, 679, 112, 1298, 998, 190, 1746]
tweetIdsCount -  3045
Expected:  [0, 48, 1, 11, 679, 112, 1746, 998, 190, 1155]
Predicted: [0, 48, 1, 11, 679, 112, 1746, 998, 190, 1298]
[1.0, 1.0, 1.0, 1.0, 0.6, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.8, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 0.9, 0.8, 0.7, 0.8, 0.9, 1.0, 0.8, 1.0, 1.0, 0.8, 0.9, 1.0, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 1.0, 0.8, 1.0, 1.0, 1.0, 0.8, 1.0, 0.9, 0.9, 1.0, 1.0, 0.8, 1.0, 0.8, 1.0, 0.9, 1.0, 1.0, 0.9, 0.9, 1.0, 1.0, 0.8, 1.0, 1.0, 0.7, 0.8, 1.0, 1.0, 1.0, 0.3, 1.0, 0.9, 1.0, 1.0, 0.9, 1.0, 0.8, 1.0, 1.0, 1.0, 0.9, 1.0, 1.0, 0.9, 0.8, 1.0, 0.9, 1.0, 1.0, 1.0, 1.0, 1.0, 0.8, 0.5, 0.8, 0.8, 0.8, 0.8, 0.7, 0.8, 0.8, 0.8, 0.8, 0.8, 0.5, 0.7, 0.8, 1.0, 0.5, 0.9, 0.9, 0.9, 0.7, 0.7, 0.8, 1.0, 0.9, 0.7, 1.0, 1.0, 0.9, 0.7, 0.7, 0.8,

In [38]:
import wordninja

In [45]:
 
X, y = generate_data()
yhat = model.predict(X)
print('Expected:  %s' % one_hot_decode(y))
print('Predicted: %s' % one_hot_decode(yhat))
arrayPredicted = numpy.array(one_hot_decode(yhat))
print("")
print("***Trending words***")
for x in arrayPredicted:
    a = re.sub('([#])|([^a-zA-Z])',' ',trendingTopicsAll[x] )
    b = wordninja.split(a)
    for y in b:
        print(y, end=' ')
    print(end='\n')

tweetIdsCount -  3060
Expected:  [0, 48, 679, 998, 1, 525, 1746, 1846, 1606, 256]
Predicted: [0, 48, 679, 998, 1, 525, 1746, 1846, 1606, 256]

***Trending words***
travel 
vacation 
tourist 
trip 
news 
traveling 
insta travel 
travel photography 
travel gram 
holidays 
